# 🧠 Gym Progress Analysis – User: Kuba

---

## 📋 Overview

This notebook presents an exploratory data analysis (EDA) of gym training data for a single user: **Kuba**.  
The goal is to understand his training patterns, volume progression, performance changes over time, and relationships between training variables (e.g. sleep, mood, stress).

We will use data loaded from an SQLite database that contains structured records of:

- Training sessions (date, bodyweight, mood, measurements, etc.)
- Exercises (name, muscle group, weight, reps)
- Additional context (program phase, duration, stress level)

---

## 🎯 Objectives

- Visualize training frequency and exercise history
- Track progression of specific lifts (e.g. Bench Press, Deadlift)
- Analyze weekly training volume per muscle group
- Examine correlations between training variables
- Prepare data for future modeling (e.g. predicting strength or body changes)

---


In [1]:
import os
import sys
import pandas as pd
import plotly.express as px
from database.queries import get_all_users
from dataframe_builder import build_user_dataframe


In [ ]:
# # Ustawiamy zmienną środowiskową DB_NAME na ścieżkę do bazy (np. jeden poziom wyżej od katalogu `analysis`)
# os.environ["DB_NAME"] = "../workout_data_base.db"
# print(os.getenv("DB_NAME", "workout_data_base.db"))

../workout_data_base.db


In [ ]:
# # # Określamy ścieżkę do katalogu głównego projektu (relatywnie do bieżącego miejsca uruchomienia notebooka)
# project_root = os.path.abspath("..")
# # # Dodajemy katalog główny do sys.path, aby Python mógł znaleźć pakiet 'database'
# sys.path.insert(0, project_root)
# # # Teraz importujemy potrzebne funkcje z modułu database.queries

In [3]:
person = get_all_users()
print(person)

[(1, 'Kuba', 'kuba@example.com'), (2, 'Anna', 'anna@example.com')]


In [4]:
df = build_user_dataframe(1)
df

session_id training_day        date  body_weight   mood  dchest  arms  \
0               1    FULLBODY1  2012-01-02         70.1  tired    82.8  25.2   
1               1    FULLBODY1  2012-01-02         70.1  tired    82.8  25.2   
2               1    FULLBODY1  2012-01-02         70.1  tired    82.8  25.2   
3               1    FULLBODY1  2012-01-02         70.1  tired    82.8  25.2   
4               1    FULLBODY1  2012-01-02         70.1  tired    82.8  25.2   
...           ...          ...         ...          ...    ...     ...   ...   
13995        2000    FULLBODY2  2024-10-09        110.7   okay   132.9  39.1   
13996        2000    FULLBODY2  2024-10-09        110.7   okay   132.9  39.1   
13997        2000    FULLBODY2  2024-10-09        110.7   okay   132.9  39.1   
13998        2000    FULLBODY2  2024-10-09        110.7   okay   132.9  39.1   
13999        2000    FULLBODY2  2024-10-09        110.7   okay   132.9  39.1   

       waist  legs  shoulders  training_duration_minutes  sleep_hours  \
0       60.4  45.7       98.6                       71.5          6.4   
1       60.4  45.7       98.6                       71.5          6.4   
2       60.4  45.7       98.6                       71.5          6.4   
3       60.4  45.7       98.6                       71.5          6.4   
4       60.4  45.7       98.6                       71.5          6.4   
...      ...   ...        ...                        ...          ...   
13995   93.5  71.1      155.8                       59.4          7.2   
13996   93.5  71.1      155.8                       59.4          7.2   
13997   93.5  71.1      155.8                       59.4          7.2   
13998   93.5  71.1      155.8                       59.4          7.2   
13999   93.5  71.1      155.8                       59.4          7.2   

       stress_level program_phase                  exercise muscle_group  \
0                 3        deload                Back Squat         legs   
1                 3        deload       Barbell Bench Press        chest   
2                 3        deload              Lat Pulldown         back   
3                 3        deload         Romanian Deadlift   hamstrings   
4                 3        deload              Assisted Dip      triceps   
...             ...           ...                       ...          ...   
13995             3   hypertrophy  Chest-Supported TBar-Row         back   
13996             3   hypertrophy             Leg Extension        quads   
13997             3   hypertrophy                Cable Flye        chest   
13998             3   hypertrophy                    Crunch         core   
13999             3   hypertrophy    Dumbbell Skull Crusher      triceps   

       weight  reps  volume  
0        39.4     9   354.6  
1        39.9     8   319.2  
2        35.6    10   356.0  
3        37.1     4   148.4  
4        20.1    11   221.1  
...       ...   ...     ...  
13995    38.9     4   155.6  
13996    35.7    11   392.7  
13997    23.1     5   115.5  
13998    24.7     8   197.6  
13999    21.3    12   255.6  

[14000 rows x 19 columns]

In [5]:
df['session_id'].unique()

array([   1,    2,    3, ..., 1998, 1999, 2000], shape=(2000,))

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14000 entries, 0 to 13999
Data columns (total 19 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   session_id                 14000 non-null  int64  
 1   training_day               14000 non-null  object 
 2   date                       14000 non-null  object 
 3   body_weight                14000 non-null  float64
 4   mood                       14000 non-null  object 
 5   dchest                     14000 non-null  float64
 6   arms                       14000 non-null  float64
 7   waist                      14000 non-null  float64
 8   legs                       14000 non-null  float64
 9   shoulders                  14000 non-null  float64
 10  training_duration_minutes  14000 non-null  float64
 11  sleep_hours                14000 non-null  float64
 12  stress_level               14000 non-null  int64  
 13  program_phase              14000 non-null  obj

In [44]:
muscle_group_counts = df['muscle_group'].value_counts().reset_index()
muscle_group_counts

muscle_group  count
0          back   2667
1         chest   2000
2       triceps   1334
3          legs   1333
4    hamstrings   1333
5     shoulders   1333
6        calves    667
7        biceps    667
8         quads    667
9          core    667
10       glutes    666
11   rear_delts    666

In [7]:
fig = px.pie(df, names = "exercise")
fig.show()

In [23]:
fig = px.scatter(df, x='date', y = 'body_weight', template="plotly_dark")
fig.show()

In [16]:
px.bar(df, x ='sleep_hours', y = 'stress_level', color = 'mood')

In [9]:
bp = df[df['exercise'] == 'Barbell Bench Press']
bp

session_id training_day        date  body_weight   mood  dchest  arms  \
1               1    FULLBODY1  2012-01-02         70.1  tired    82.8  25.2   
22              4    FULLBODY1  2012-01-09         70.3   okay    85.4  24.0   
43              7    FULLBODY1  2012-01-15         70.2   okay    85.3  24.5   
64             10    FULLBODY1  2012-01-23         70.6  tired    84.5  24.5   
85             13    FULLBODY1  2012-01-30         70.5   good    83.9  24.4   
...           ...          ...         ...          ...    ...     ...   ...   
13903        1987    FULLBODY1  2024-09-09        110.3  tired   134.0  38.5   
13924        1990    FULLBODY1  2024-09-14        110.4  tired   133.0  39.4   
13945        1993    FULLBODY1  2024-09-23        110.4   okay   133.6  38.2   
13966        1996    FULLBODY1  2024-09-30        110.7   okay   132.8  38.0   
13987        1999    FULLBODY1  2024-10-07        110.6   okay   134.8  38.9   

       waist  legs  shoulders  training_duration_minutes  sleep_hours  \
1       60.4  45.7       98.6                       71.5          6.4   
22      60.9  45.6       98.4                       55.1          7.8   
43      59.2  47.3       97.5                       58.0          7.6   
64      61.2  46.1      100.1                       59.9          6.5   
85      60.7  45.6       99.8                       61.2          8.8   
...      ...   ...        ...                        ...          ...   
13903   94.6  71.9      154.6                       64.5          6.3   
13924   93.6  71.9      154.0                       66.3          6.1   
13945   92.6  71.1      152.4                       65.5          7.9   
13966   95.7  70.6      154.2                       59.0          7.4   
13987   94.0  73.7      154.2                       63.2          7.2   

       stress_level program_phase             exercise muscle_group  weight  \
1                 3        deload  Barbell Bench Press        chest    39.9   
22                1   hypertrophy  Barbell Bench Press        chest    39.8   
43                2   hypertrophy  Barbell Bench Press        chest    40.4   
64                2   hypertrophy  Barbell Bench Press        chest    40.9   
85                1   hypertrophy  Barbell Bench Press        chest    40.1   
...             ...           ...                  ...          ...     ...   
13903             3   hypertrophy  Barbell Bench Press        chest    48.1   
13924             1   hypertrophy  Barbell Bench Press        chest    49.4   
13945             1        deload  Barbell Bench Press        chest    48.1   
13966             3   hypertrophy  Barbell Bench Press        chest    47.2   
13987             6   hypertrophy  Barbell Bench Press        chest    48.6   

       reps  volume  
1         8   319.2  
22        7   278.6  
43        8   323.2  
64       10   409.0  
85        9   360.9  
...     ...     ...  
13903     8   384.8  
13924     6   296.4  
13945     8   384.8  
13966     7   330.4  
13987     8   388.8  

[667 rows x 19 columns]

In [10]:
px.scatter(bp, x = 'date', y = 'weight', color = 'mood')

In [11]:
px.histogram(bp, x = 'weight', color = 'mood')

In [15]:
px.scatter(bp, x = 'dchest', y = "weight", color = 'mood')

In [1]:
while(True):
    print("s")

s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s
s


: 